In [1]:
import os
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from bs4 import BeautifulSoup
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
import time
import re
import pandas as pd
import numpy as np

In [2]:
processo = list()
agencia_envolvida = list()
turma = list()
data_julgamento = list()
data_publicacao = list()
relator = list()
links = list()

# APELANTE
# 'Agência Nacional de Telecomunicações' (29), 'Agência Nacional de Energia Elétrica' (3), 'Agência Nacional do Cinema' (9), 
# 'Agência Nacional de Aviação Civil' (5), 'Agência Nacional de Transportes Aquaviários' (2), 'Agência Nacional de Transportes Terrestres' (60), 
# 'Agência Nacional do Petróleo, Gás Natural e Biocombustíveis' (108), 'Agência Nacional de Vigilância Sanitária' (23), 'Agência Nacional de Saúde' (208), 
# 'Agência Nacional de Mineração' (1 'Agência Naciona de Mineração')

# APELADO
# 'Agência Nacional de Telecomunicações' (59), 'Agência Nacional de Energia Elétrica' (13), 'Agência Nacional do Cinema' (39), 
# 'Agência Nacional de Aviação Civil' (17), 'Agência Nacional de Transportes Aquaviários' (4), 'Agência Nacional de Transportes Terrestres' (70), 
# 'Agência Nacional do Petróleo, Gás Natural e Biocombustíveis' (146), 'Agência Nacional de Vigilância Sanitária' (39), 'Agência Nacional de Saúde' (495), 
# 'Agência Nacional de Mineração' (0 'Agência Naciona de Mineração')

agencias = ['Agência.Nacional.de.Saúde']

for agencia in agencias:
    path = 'D:/HD_externo_yas/Faculdade/Assistencia_de_pesquisa'
    final_path = 'D:/HD externo yas/Faculdade/Assistencia de pesquisa'

    chrome_options = Options()
    chrome_options.add_argument("--window-size=1240,1080") # define o tamanho da janela a ser aberta
    driver = webdriver.Chrome(executable_path = os.path.join(path,'chromedriver.exe'), options = chrome_options) # o path do chromedriver
    url1 = 'https://www10.trf2.jus.br/consultas/?q=Apelado.%3A.' #q=Apelante.%3A.
    url2 = '+-agravo+-embargo+-embargos+-agravos&site=v2_jurisprudencia&client=v2_index&proxystylesheet=v2_index&filter=0&getfields=*&lr=lang_pt&oe=UTF-8&ie=UTF-8&output=xml_no_dtd&sort=date%3AD%3AS%3Ad1&entsp=a&adv=1&base=JP-TRF&wc=200&wc_mc=0&ud=1'
    url = url1 + agencia + url2
    driver.get(url)
    
    html_source = driver.page_source
    soup = BeautifulSoup(html_source,"html.parser")

    body = driver.find_element(By.TAG_NAME, 'body')
    for i in range(10):
        body.send_keys(Keys.DOWN)

    time.sleep(3)
    link = WebDriverWait(driver, 5).until(EC.element_to_be_clickable((By.XPATH, "//a[@title='Inteiro Teor']")))
    link.click()

    for pagina in range(60):

        html_source = driver.page_source
        soup = BeautifulSoup(html_source,"html.parser")
        # salvando a página encontrada pela busca

        body = driver.find_element(By.TAG_NAME, 'body')
        for i in range(60):
            body.send_keys(Keys.DOWN)
            #time.sleep(0.5)

        divs = soup.find_all('div', {'class': 'title-doc'})
        time.sleep(2)
        for div in divs:
            span = div.find('span', {'id': lambda x: x and x.startswith('ementa-')})
            agencia_envolvida.append(agencia)
            if span:
                processo.append(span.get_text())

        divs2 = soup.find_all('div', {'class': 'doc-text'})
        time.sleep(2)
        for div in divs2:
            span2 = div.find('span', {'class': 'gsa-orgJulg'})
            if span2:
                turma.append(span2.get_text())
        
        divs3 = soup.find_all('div', {'class': 'data-relator'})
        time.sleep(2)
        for div in divs3:
            datas = div.find_all('span', {'class': 'valor'})
            span3 = datas[0]
            span4 = datas[1]
            span5 = div.find('span', {'class': 'valor gsa-relator'})
            if span3:
                data_julgamento.append(span3.get_text())
            if span4:
                data_publicacao.append(span4.get_text())
            if span5:
                relator.append(span5.get_text())

        divs4 = soup.find_all('div', {'class': 'tipo_doc'})
        time.sleep(2)
        for div in divs4:
            botao = div.select_one('a.font_bold[href*="?movimento"]')
            if botao:
                link = botao['href']
                links.append(link)

        if pagina == 0:
        # Use the selector for the second page link
            selector = '//*[@id="bottom-navigation"]/div[1]/span[2]/a'
        else:
        # Use the selector for the next page link
            selector = '//*[@id="bottom-navigation"]/div[1]/span[4]/a'

        # check if a new tab has been opened
        if len(driver.window_handles) > 1:
            # switch back to the original tab
            driver.switch_to.window(driver.window_handles[0])
            time.sleep(3)  # wait for the page to load
            driver.refresh()  # refresh the page
            # find the elements again
            driver.find_element(by=By.XPATH, value='//*[@id="bottom-navigation"]/div[1]/span[4]/a').click()
        else:
             # Find the element using the appropriate selector
            try:
                driver.find_element(by=By.XPATH, value=selector).click()
                time.sleep(2)
            except:
                pass
                break
        #driver.switch_to.window(driver.window_handles[0])


    driver.quit()

C:\Users\fabio\AppData\Local\Temp\ipykernel_12728\4284347171.py:29: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(executable_path = os.path.join(path,'chromedriver.exe'), options = chrome_options) # o path do chromedriver


In [3]:
dados = {'processo': processo,
         'agencia_envolvida': agencia_envolvida,
         'turma': turma,
         'data_julgamento': data_julgamento,
         'data_publicacao': data_publicacao,
         'relator': relator,
         'links': links}

In [4]:
df = pd.DataFrame.from_dict(dados, orient='index')
df = df.transpose()
df['links'] = 'https://www10.trf2.jus.br/consultas/' + df['links'].astype(str)
df

processo  \
0    0006767-26.2016.4.02.5101 (TRF2 2016.51.01.006...   
1    0002752-77.2017.4.02.5101 (TRF2 2017.51.01.002...   
2    0043283-84.2012.4.02.5101 (TRF2 2012.51.01.043...   
3    0111691-25.2015.4.02.5004 (TRF2 2015.50.04.111...   
4    0017681-57.2013.4.02.5101 (TRF2 2013.51.01.017...   
..                                                 ...   
490  0020517-23.2001.4.02.5101 (TRF2 2001.51.01.020...   
491  0005466-69.2001.4.02.5101 (TRF2 2001.51.01.005...   
492  0023871-33.2001.4.02.0000 (TRF2 2001.02.01.023...   
493  0033286-40.2001.4.02.0000 (TRF2 2001.02.01.033...   
494  0040416-81.2001.4.02.0000 (TRF2 2001.02.01.040...   

             agencia_envolvida                   turma data_julgamento  \
0    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      04/03/2021   
1    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      15/12/2020   
2    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      18/12/2019   
3    Agência.Nacional.de.Saúde  5ª TURMA ESPECIALIZADA      16/12/2019   
4    Agência.Nacional.de.Saúde  7ª TURMA ESPECIALIZADA      08/11/2019   
..                         ...                     ...             ...   
490  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      18/11/2002   
491  Agência.Nacional.de.Saúde            QUARTA TURMA      11/09/2002   
492  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   
493  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   
494  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   

    data_publicacao                  relator  \
0        09/03/2021          VERA LÚCIA LIMA   
1        17/12/2020  GUILHERME DIEFENTHAELER   
2        20/12/2019          VERA LÚCIA LIMA   
3        18/12/2019            VIGDOR TEITEL   
4        25/11/2019    FLAVIO OLIVEIRA LUCAS   
..              ...                      ...   
490      08/05/2003       JULIETA LIDIA LUNZ   
491      05/06/2003         ROGERIO CARVALHO   
492      30/08/2002           CARREIRA ALVIM   
493      30/08/2002           CARREIRA ALVIM   
494      30/08/2002           CARREIRA ALVIM   

                                                 links  
0    https://www10.trf2.jus.br/consultas/?movimento...  
1    https://www10.trf2.jus.br/consultas/?movimento...  
2    https://www10.trf2.jus.br/consultas/?movimento...  
3    https://www10.trf2.jus.br/consultas/?movimento...  
4    https://www10.trf2.jus.br/consultas/?movimento...  
..                                                 ...  
490  https://www10.trf2.jus.br/consultas/?movimento...  
491  https://www10.trf2.jus.br/consultas/?movimento...  
492  https://www10.trf2.jus.br/consultas/?movimento...  
493  https://www10.trf2.jus.br/consultas/?movimento...  
494  https://www10.trf2.jus.br/consultas/?movimento...  

[495 rows x 7 columns]

In [5]:
df['numero_processo'] = df['processo'].str.extract(r'(\b\d{4}\.\d{2}\.\d{2}\.\d{6}-\d\b)')
df['numero_processo'] = df['numero_processo'].str.replace('.','')
df['numero_processo'] = df['numero_processo'].str.replace('-','')

C:\Users\fabio\AppData\Local\Temp\ipykernel_12728\3066792417.py:2: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df['numero_processo'] = df['numero_processo'].str.replace('.','')


In [6]:
links_list = df.links.values.tolist()
print(links_list)

['https://www10.trf2.jus.br/consultas/?movimento=cache&q=cache:Ie86kakJvYgJ:acordaos.trf2.jus.br/apolo/databucket/idx%3Fprocesso%3D201651010067674%26coddoc%3D805306%26datapublic%3D2021-03-10%26pagdj%3D194/199+Apelado.:.Ag%C3%AAncia.Nacional.de.Sa%C3%BAde+-agravo+-embargo+-embargos+-agravos+inmeta:gsaentity_BASE%3DInteiro%2520Teor&site=v2_jurisprudencia&client=v2_index&proxystylesheet=v2_index&lr=lang_pt&ie=UTF-8&output=xml_no_dtd&access=p&oe=UTF-8', 'https://www10.trf2.jus.br/consultas/?movimento=cache&q=cache:cPHPs8w8OMQJ:acordaos.trf2.jus.br/apolo/databucket/idx%3Fprocesso%3D201751010027528%26coddoc%3D2344589%26datapublic%3D2020-12-18%26pagdj%3D589/598+Apelado.:.Ag%C3%AAncia.Nacional.de.Sa%C3%BAde+-agravo+-embargo+-embargos+-agravos+inmeta:gsaentity_BASE%3DInteiro%2520Teor&site=v2_jurisprudencia&client=v2_index&proxystylesheet=v2_index&lr=lang_pt&ie=UTF-8&output=xml_no_dtd&access=p&oe=UTF-8', 'https://www10.trf2.jus.br/consultas/?movimento=cache&q=cache:X9qCvWt2z1UJ:acordaos.trf2.jus

In [107]:
#links_list = links_list[-11:]
#print(links_list)

['https://www10.trf2.jus.br/consultas/?movimento=cache&q=cache:kTcuNDhQ-2sJ:trf2nas.trf.net/iteor/TXT/RJ0106610/1/27/85116.rtf+Apelante.:.Ag%C3%AAncia.Nacional.de.Sa%C3%BAde+-agravo+-embargo+-embargos+-agravos+inmeta:gsaentity_BASE%3DInteiro%2520Teor&site=v2_jurisprudencia&client=v2_index&proxystylesheet=v2_index&lr=lang_pt&ie=UTF-8&output=xml_no_dtd&access=p&oe=UTF-8', 'https://www10.trf2.jus.br/consultas/?movimento=cache&q=cache:SpYAUG4lQWMJ:trf2nas.trf.net/iteor/TXT/RJ0106610/1/27/85107.rtf+Apelante.:.Ag%C3%AAncia.Nacional.de.Sa%C3%BAde+-agravo+-embargo+-embargos+-agravos+inmeta:gsaentity_BASE%3DInteiro%2520Teor&site=v2_jurisprudencia&client=v2_index&proxystylesheet=v2_index&lr=lang_pt&ie=UTF-8&output=xml_no_dtd&access=p&oe=UTF-8', 'https://www10.trf2.jus.br/consultas/?movimento=cache&q=cache:fxDYssxgLkYJ:trf2nas.trf.net/iteor/TXT/RJ0106610/1/27/85085.rtf+Apelante.:.Ag%C3%AAncia.Nacional.de.Sa%C3%BAde+-agravo+-embargo+-embargos+-agravos+inmeta:gsaentity_BASE%3DInteiro%2520Teor&site=

In [8]:
teores_text = list()
count = 0

for link in links_list:
    teores_str = list()
    count += 1
    print(count)
    path = 'D:/HD_externo_yas/Faculdade/Assistencia_de_pesquisa'
    final_path = 'D:/HD externo yas/Faculdade/Assistencia de pesquisa'
    
    chrome_options = Options()
    chrome_options.add_argument("--window-size=1240,1080") # define o tamanho da janela a ser aberta
    driver = webdriver.Chrome(executable_path = os.path.join(path,'chromedriver.exe'), options = chrome_options) # o path do chromedriver
    url = link
    driver.get(url)

    time.sleep(8)

    html_source = driver.page_source
    soup = BeautifulSoup(html_source,"html.parser") # salvando a página encontrada pela busca

    #texto = soup.find_all('span',{'style':'font-size:16px;font-family:Times'})
    for nobr in soup.find_all('nobr'):
        teores_str.append(nobr.get_text().strip())

    for td in soup.find_all('td'):
        teores_str.append(td.get_text().strip())

    for font in soup.find_all('font'):
        teores_str.append(font.get_text().strip())
    
    teores_str = ' '.join(teores_str)
    teores_text.append(teores_str)
    
    driver.quit()

df['teor'] = pd.Series(teores_text)

1


C:\Users\fabio\AppData\Local\Temp\ipykernel_12728\4118593247.py:13: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(executable_path = os.path.join(path,'chromedriver.exe'), options = chrome_options) # o path do chromedriver


2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
27

In [9]:
df['teor'] = df['teor'].str.replace('\xa0',' ')
df['teor'] = df['teor'].str.replace('\n',' ')
df

processo  \
0    0006767-26.2016.4.02.5101 (TRF2 2016.51.01.006...   
1    0002752-77.2017.4.02.5101 (TRF2 2017.51.01.002...   
2    0043283-84.2012.4.02.5101 (TRF2 2012.51.01.043...   
3    0111691-25.2015.4.02.5004 (TRF2 2015.50.04.111...   
4    0017681-57.2013.4.02.5101 (TRF2 2013.51.01.017...   
..                                                 ...   
490  0020517-23.2001.4.02.5101 (TRF2 2001.51.01.020...   
491  0005466-69.2001.4.02.5101 (TRF2 2001.51.01.005...   
492  0023871-33.2001.4.02.0000 (TRF2 2001.02.01.023...   
493  0033286-40.2001.4.02.0000 (TRF2 2001.02.01.033...   
494  0040416-81.2001.4.02.0000 (TRF2 2001.02.01.040...   

             agencia_envolvida                   turma data_julgamento  \
0    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      04/03/2021   
1    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      15/12/2020   
2    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      18/12/2019   
3    Agência.Nacional.de.Saúde  5ª TURMA ESPECIALIZADA      16/12/2019   
4    Agência.Nacional.de.Saúde  7ª TURMA ESPECIALIZADA      08/11/2019   
..                         ...                     ...             ...   
490  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      18/11/2002   
491  Agência.Nacional.de.Saúde            QUARTA TURMA      11/09/2002   
492  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   
493  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   
494  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   

    data_publicacao                  relator  \
0        09/03/2021          VERA LÚCIA LIMA   
1        17/12/2020  GUILHERME DIEFENTHAELER   
2        20/12/2019          VERA LÚCIA LIMA   
3        18/12/2019            VIGDOR TEITEL   
4        25/11/2019    FLAVIO OLIVEIRA LUCAS   
..              ...                      ...   
490      08/05/2003       JULIETA LIDIA LUNZ   
491      05/06/2003         ROGERIO CARVALHO   
492      30/08/2002           CARREIRA ALVIM   
493      30/08/2002           CARREIRA ALVIM   
494      30/08/2002           CARREIRA ALVIM   

                                                 links  numero_processo  \
0    https://www10.trf2.jus.br/consultas/?movimento...  201651010067674   
1    https://www10.trf2.jus.br/consultas/?movimento...  201751010027528   
2    https://www10.trf2.jus.br/consultas/?movimento...  201251010432838   
3    https://www10.trf2.jus.br/consultas/?movimento...  201550041116913   
4    https://www10.trf2.jus.br/consultas/?movimento...  201351010176814   
..                                                 ...              ...   
490  https://www10.trf2.jus.br/consultas/?movimento...  200151010205174   
491  https://www10.trf2.jus.br/consultas/?movimento...  200151010054664   
492  https://www10.trf2.jus.br/consultas/?movimento...  200102010238712   
493  https://www10.trf2.jus.br/consultas/?movimento...  200102010332868   
494  https://www10.trf2.jus.br/consultas/?movimento...  200102010404168   

                                                  teor  
0    E M E N T A A D M I N I S T R A T I V O . O P ...  
1     E M E N T A  APELAÇÃO CÍVEL. PROCESSO ADMINIS...  
2     E M E N T A PROCESSUAL CIVIL. DESISTÊNCIA DA ...  
3    Apelação Cível - Turma Espec. III - Administra...  
4    Apelação Cível - Turma Espec. III - Administra...  
..                                                 ...  
490  RELATOR : DESEMBARGADOR FEDERAL NEY FONSECA AP...  
491  RELATOR : DESEMBARGADOR FEDERAL ROGERIO CARVAL...  
492  RELATOR : DESEMBARGADOR FEDERAL CARREIRA ALVIM...  
493  RELATOR : DESEMBARGADOR FEDERAL CARREIRA ALVIM...  
494  RELATOR : DESEMBARGADOR FEDERAL CARREIRA ALVIM...  

[495 rows x 9 columns]

In [172]:
#df.loc[121,:]
#df = df.drop([df.index[121]]).reset_index(drop=True)

In [10]:
teores_list = df.teor.values.tolist()
print(teores_list)

['E M E N T A A D M I N I S T R A T I V O . O P E R A D O R A D E P L A N O D E S A Ú D E . REDUÇÃO/REDIMENSIONAMENTO DA REDE HOSPITALAR SEM AUTORIZAÇÃO DA ANS. VIOLAÇÃO AO ART. 17, §4º, DA LEI 9.656/98. LEGALIDADE E PROPORCIONALIDADE DA SANÇÃO IMPOSTA. RECURSO DESPROVIDO. -Cinge-se a controvérsia em verificar a adequação da sanção administrativa imposta à autora, em virtude da prática de infração administrativa prevista no art. 17 da Lei 9.656/98. - No tocante ao cerne da demanda posta a deslinde, verifica-se que a autora não infirma os fatos que deram ensejo à imposição da sanção, mas defende a inexigibilidade da multa aplicada, sob o argumento de que não solicitou o redimensionamento/redução de sua rede hospitalar, porquanto a rescisão do contrato teria partido dos prestadores. Por conseguinte, sua conduta não se amoldaria ao preceito sancionador. -No entanto, em que pese a argumentação expendida, o art. 17, §4º, da Lei 9.656/98, dispõe expressamente que: “em caso de redimensionamen

In [11]:
#teores_list[124] #apagar

In [12]:
apelante_1 = list()
apelado_1 = list()
ementa = list()
count = 0

for teor in teores_list: 
    count += 1
    print(count)
    try:
        match_ementa = re.search(r"(?<=[Ee][Mm][Ee][Nn][Tt][Aa][\s:])[^\n\r]+?(?=\s*(?:\s[Aa][Cc][Óó][Rr][Dd][Ãã][Oo]|$))", teor).group(0)
        ementa.append(match_ementa)
    except: 
        try:
            match_ementa = re.search(r"(?<=E\sM\sE\sN\sT\sA[\s:])([^\n\r])+?(?=\s*(?:\sA\sC\sÓ\sR\sD\sÃ\sO|$))", teor).group(0)
            ementa.append(match_ementa)
        except:
            match_ementa = re.search(r"(?<=E\s\sM\s\sE\s\sN\s\sT\s\sA[\s:])([^\n\r])+?(?=\s*(?:\sA\s\sC\s\sÓ\s\sR\s\sD\s\sÃ\s\sO|$))", teor).group(0)
            ementa.append(match_ementa)
    match_apelante_1 = re.findall(r"(?<=APELANTE\s:\s)[^\n\r]+?(?=\s*(?:ADVOGADO|PROCURADOR|APELADO|$))", teor)
    apelante_1.append(match_apelante_1)
    match_apelado_1 = re.findall(r"(?<=APELADO\s:\s)[^\n\r]+?(?=\s*(?:ADVOGADO|PROCURADOR|APELADO|$))", teor)
    apelado_1.append(match_apelado_1)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [13]:
apelante_2 = [list(set(lst)) for lst in apelante_1]
apelado_2 = [list(set(lst)) for lst in apelado_1]

In [14]:
dados_2 = {'teor': teores_list,
           'ementa': ementa,
           'apelante': apelante_2,
           'apelado': apelado_2}

df2 = pd.DataFrame.from_dict(dados_2)

In [15]:
df_int = df.merge(df2, on='teor', how='left')

In [16]:
df_int

processo  \
0    0006767-26.2016.4.02.5101 (TRF2 2016.51.01.006...   
1    0002752-77.2017.4.02.5101 (TRF2 2017.51.01.002...   
2    0043283-84.2012.4.02.5101 (TRF2 2012.51.01.043...   
3    0111691-25.2015.4.02.5004 (TRF2 2015.50.04.111...   
4    0017681-57.2013.4.02.5101 (TRF2 2013.51.01.017...   
..                                                 ...   
496  0020517-23.2001.4.02.5101 (TRF2 2001.51.01.020...   
497  0005466-69.2001.4.02.5101 (TRF2 2001.51.01.005...   
498  0023871-33.2001.4.02.0000 (TRF2 2001.02.01.023...   
499  0033286-40.2001.4.02.0000 (TRF2 2001.02.01.033...   
500  0040416-81.2001.4.02.0000 (TRF2 2001.02.01.040...   

             agencia_envolvida                   turma data_julgamento  \
0    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      04/03/2021   
1    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      15/12/2020   
2    Agência.Nacional.de.Saúde  8ª TURMA ESPECIALIZADA      18/12/2019   
3    Agência.Nacional.de.Saúde  5ª TURMA ESPECIALIZADA      16/12/2019   
4    Agência.Nacional.de.Saúde  7ª TURMA ESPECIALIZADA      08/11/2019   
..                         ...                     ...             ...   
496  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      18/11/2002   
497  Agência.Nacional.de.Saúde            QUARTA TURMA      11/09/2002   
498  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   
499  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   
500  Agência.Nacional.de.Saúde          PRIMEIRA TURMA      28/05/2002   

    data_publicacao                  relator  \
0        09/03/2021          VERA LÚCIA LIMA   
1        17/12/2020  GUILHERME DIEFENTHAELER   
2        20/12/2019          VERA LÚCIA LIMA   
3        18/12/2019            VIGDOR TEITEL   
4        25/11/2019    FLAVIO OLIVEIRA LUCAS   
..              ...                      ...   
496      08/05/2003       JULIETA LIDIA LUNZ   
497      05/06/2003         ROGERIO CARVALHO   
498      30/08/2002           CARREIRA ALVIM   
499      30/08/2002           CARREIRA ALVIM   
500      30/08/2002           CARREIRA ALVIM   

                                                 links  numero_processo  \
0    https://www10.trf2.jus.br/consultas/?movimento...  201651010067674   
1    https://www10.trf2.jus.br/consultas/?movimento...  201751010027528   
2    https://www10.trf2.jus.br/consultas/?movimento...  201251010432838   
3    https://www10.trf2.jus.br/consultas/?movimento...  201550041116913   
4    https://www10.trf2.jus.br/consultas/?movimento...  201351010176814   
..                                                 ...              ...   
496  https://www10.trf2.jus.br/consultas/?movimento...  200151010205174   
497  https://www10.trf2.jus.br/consultas/?movimento...  200151010054664   
498  https://www10.trf2.jus.br/consultas/?movimento...  200102010238712   
499  https://www10.trf2.jus.br/consultas/?movimento...  200102010332868   
500  https://www10.trf2.jus.br/consultas/?movimento...  200102010404168   

                                                  teor  \
0    E M E N T A A D M I N I S T R A T I V O . O P ...   
1     E M E N T A  APELAÇÃO CÍVEL. PROCESSO ADMINIS...   
2     E M E N T A PROCESSUAL CIVIL. DESISTÊNCIA DA ...   
3    Apelação Cível - Turma Espec. III - Administra...   
4    Apelação Cível - Turma Espec. III - Administra...   
..                                                 ...   
496  RELATOR : DESEMBARGADOR FEDERAL NEY FONSECA AP...   
497  RELATOR : DESEMBARGADOR FEDERAL ROGERIO CARVAL...   
498  RELATOR : DESEMBARGADOR FEDERAL CARREIRA ALVIM...   
499  RELATOR : DESEMBARGADOR FEDERAL CARREIRA ALVIM...   
500  RELATOR : DESEMBARGADOR FEDERAL CARREIRA ALVIM...   

                                                ementa  \
0    A D M I N I S T R A T I V O . O P E R A D O R ...   
1     APELAÇÃO CÍVEL. PROCESSO ADMINISTRATIVO. AGÊN...   
2    PROCESSUAL CIVIL. DESISTÊNCIA DA AÇÃO EM FASE ...   
3     ADMINISTRATIVO. UNIMED. MIOMECTOMIA UTERINA. ..

In [17]:
df_int["apelante"] = df_int["apelante"].astype(str)
df_int["apelado"] = df_int["apelado"].astype(str)

In [18]:
df_int['apelante'] = df_int['apelante'].str.replace('[','')
df_int['apelante'] = df_int['apelante'].str.replace(']','')

df_int['apelado'] = df_int['apelado'].str.replace('[','')
df_int['apelado'] = df_int['apelado'].str.replace(']','')

df_int['apelado'] = df_int['apelado'].str.replace("'",'')
df_int['apelante'] = df_int['apelante'].str.replace("'",'')

C:\Users\fabio\AppData\Local\Temp\ipykernel_12728\2230384222.py:1: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_int['apelante'] = df_int['apelante'].str.replace('[','')
C:\Users\fabio\AppData\Local\Temp\ipykernel_12728\2230384222.py:2: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_int['apelante'] = df_int['apelante'].str.replace(']','')
C:\Users\fabio\AppData\Local\Temp\ipykernel_12728\2230384222.py:4: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_int['apelado'] = df_int['apelado'].str.replace('[','')
C:\Users\

In [19]:
df_int = df_int.reindex(columns=["processo", "numero_processo", "turma","data_julgamento","data_publicacao","agencia_envolvida","relator","apelante","apelado","teor","ementa","links"])
df_int = df_int.drop(['processo', 'teor', 'links'], axis=1)
df_int

numero_processo                   turma data_julgamento data_publicacao  \
0    201651010067674  8ª TURMA ESPECIALIZADA      04/03/2021      09/03/2021   
1    201751010027528  8ª TURMA ESPECIALIZADA      15/12/2020      17/12/2020   
2    201251010432838  8ª TURMA ESPECIALIZADA      18/12/2019      20/12/2019   
3    201550041116913  5ª TURMA ESPECIALIZADA      16/12/2019      18/12/2019   
4    201351010176814  7ª TURMA ESPECIALIZADA      08/11/2019      25/11/2019   
..               ...                     ...             ...             ...   
496  200151010205174          PRIMEIRA TURMA      18/11/2002      08/05/2003   
497  200151010054664            QUARTA TURMA      11/09/2002      05/06/2003   
498  200102010238712          PRIMEIRA TURMA      28/05/2002      30/08/2002   
499  200102010332868          PRIMEIRA TURMA      28/05/2002      30/08/2002   
500  200102010404168          PRIMEIRA TURMA      28/05/2002      30/08/2002   

             agencia_envolvida                  relator  \
0    Agência.Nacional.de.Saúde          VERA LÚCIA LIMA   
1    Agência.Nacional.de.Saúde  GUILHERME DIEFENTHAELER   
2    Agência.Nacional.de.Saúde          VERA LÚCIA LIMA   
3    Agência.Nacional.de.Saúde            VIGDOR TEITEL   
4    Agência.Nacional.de.Saúde    FLAVIO OLIVEIRA LUCAS   
..                         ...                      ...   
496  Agência.Nacional.de.Saúde       JULIETA LIDIA LUNZ   
497  Agência.Nacional.de.Saúde         ROGERIO CARVALHO   
498  Agência.Nacional.de.Saúde           CARREIRA ALVIM   
499  Agência.Nacional.de.Saúde           CARREIRA ALVIM   
500  Agência.Nacional.de.Saúde           CARREIRA ALVIM   

                                              apelante  \
0         AMIL - ASSISTENCIA MEDICA INTERNACIONAL S.A.   
1     UNIMED DO ESTADO DE MATO GROSSO DO SUL - FEDE...   
2         AMIL - ASSISTENCIA MEDICA INTERNACIONAL LTDA   
3    UNIMED NORTE CAPIXABA COOPERATIVA DE TRABALHO ...   
4                        PLANO DE SAÚDE ANA COSTA LTDA   
..                                                 ...   
496                             INTERMEDICA SAUDE LTDA   
497     UNIMED PENEDO - COOPERATIVA DE TRABALHO MEDICO   
498  UNIMED VICOSA - COOPERATIVA DE TRABALHO MEDICO...   
499  UNIMED JOAO PESSOA - COOPERATIVA DE TRABALHO M...   
500  UNIMED PARA DE MINAS - COOPERATIVA DE TRABALHO...   

                                         apelado  \
0    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
1    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
2    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
3    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
4    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
..                                           ...   
496    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR-ANS   
497                AGENCIA NACIONAL DE SAUDE-ANS   
498  AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
499  AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
500  AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   

                                                ementa  
0    A D M I N I S T R A T I V O . O P E R A D O R ...  
1     APELAÇÃO CÍVEL. PROCESSO ADMINISTRATIVO. AGÊN...  
2    PROCESSUAL CIVIL. DESISTÊNCIA DA AÇÃO EM FASE ...  
3     ADMINISTRATIVO. UNIMED. MIOMECTOMIA UTERINA. ...  
4      APELAÇÃO. RESSARCIMENTO AO SUS. NULIDADE. SE...  
..                                                 ...  
496  PROCESSO CIVIL - EXTINÇÃO DO FEITO - REQUERIME...  
497  de julgado do STF, transcrito às fls. 299: “I....  
498  TRIBUTÁRIO - TAXA SUPLEMENTAR DE SAÚDE - LEI N...  
499  TRIBUTÁRIO - TAXA SUPLEMENTAR DE SAÚDE - LEI N...  
500  TRIBUTÁRIO - TAXA SUPLEMENTAR DE SAÚDE - LEI N...  

[501 rows x 9 columns]

In [20]:
ementas_list = df_int.ementa.values.tolist()
decisao = []

for ementa in ementas_list:
    if re.search(r"(parcial(mente)? provi(d[oa]|mento)|provid[oa](s)? em parte)", ementa):
        decisao.append("provimento parcial")
    elif re.search(r"([Nn][ãa]o |[Dd]es|[Ii]m|[Nn]egar |NÃO |NEGAR )(provid[oa]|conhecid[oa]|provimento|PROVID[OA]|PROVIMENTO)(s)?", ementa):
        decisao.append("não provimento")
    else:
        decisao.append("provimento")

df_int['decisao'] = decisao
df_int

numero_processo                   turma data_julgamento data_publicacao  \
0    201651010067674  8ª TURMA ESPECIALIZADA      04/03/2021      09/03/2021   
1    201751010027528  8ª TURMA ESPECIALIZADA      15/12/2020      17/12/2020   
2    201251010432838  8ª TURMA ESPECIALIZADA      18/12/2019      20/12/2019   
3    201550041116913  5ª TURMA ESPECIALIZADA      16/12/2019      18/12/2019   
4    201351010176814  7ª TURMA ESPECIALIZADA      08/11/2019      25/11/2019   
..               ...                     ...             ...             ...   
496  200151010205174          PRIMEIRA TURMA      18/11/2002      08/05/2003   
497  200151010054664            QUARTA TURMA      11/09/2002      05/06/2003   
498  200102010238712          PRIMEIRA TURMA      28/05/2002      30/08/2002   
499  200102010332868          PRIMEIRA TURMA      28/05/2002      30/08/2002   
500  200102010404168          PRIMEIRA TURMA      28/05/2002      30/08/2002   

             agencia_envolvida                  relator  \
0    Agência.Nacional.de.Saúde          VERA LÚCIA LIMA   
1    Agência.Nacional.de.Saúde  GUILHERME DIEFENTHAELER   
2    Agência.Nacional.de.Saúde          VERA LÚCIA LIMA   
3    Agência.Nacional.de.Saúde            VIGDOR TEITEL   
4    Agência.Nacional.de.Saúde    FLAVIO OLIVEIRA LUCAS   
..                         ...                      ...   
496  Agência.Nacional.de.Saúde       JULIETA LIDIA LUNZ   
497  Agência.Nacional.de.Saúde         ROGERIO CARVALHO   
498  Agência.Nacional.de.Saúde           CARREIRA ALVIM   
499  Agência.Nacional.de.Saúde           CARREIRA ALVIM   
500  Agência.Nacional.de.Saúde           CARREIRA ALVIM   

                                              apelante  \
0         AMIL - ASSISTENCIA MEDICA INTERNACIONAL S.A.   
1     UNIMED DO ESTADO DE MATO GROSSO DO SUL - FEDE...   
2         AMIL - ASSISTENCIA MEDICA INTERNACIONAL LTDA   
3    UNIMED NORTE CAPIXABA COOPERATIVA DE TRABALHO ...   
4                        PLANO DE SAÚDE ANA COSTA LTDA   
..                                                 ...   
496                             INTERMEDICA SAUDE LTDA   
497     UNIMED PENEDO - COOPERATIVA DE TRABALHO MEDICO   
498  UNIMED VICOSA - COOPERATIVA DE TRABALHO MEDICO...   
499  UNIMED JOAO PESSOA - COOPERATIVA DE TRABALHO M...   
500  UNIMED PARA DE MINAS - COOPERATIVA DE TRABALHO...   

                                         apelado  \
0    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
1    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
2    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
3    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
4    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
..                                           ...   
496    AGENCIA NACIONAL DE SAUDE SUPLEMENTAR-ANS   
497                AGENCIA NACIONAL DE SAUDE-ANS   
498  AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
499  AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   
500  AGENCIA NACIONAL DE SAUDE SUPLEMENTAR - ANS   

                                                ementa             decisao  
0    A D M I N I S T R A T I V O . O P E R A D O R ...      não provimento  
1     APELAÇÃO CÍVEL. PROCESSO ADMINISTRATIVO. AGÊN...      não provimento  
2    PROCESSUAL CIVIL. DESISTÊNCIA DA AÇÃO EM FASE ...          provimento  
3     ADMINISTRATIVO. UNIMED. MIOMECTOMIA UTERINA. ...      não provimento  
4      APELAÇÃO. RESSARCIMENTO AO SUS. NULIDADE. SE...  provimento parcial  
..                                                 ...                 ...  
496  PROCESSO CIVIL - EXTINÇÃO DO FEITO - REQUERIME...          provimento  
497  de julgado do STF, transcrito às fls. 299: “I....          provimento  
498  TRIBUTÁRIO - TAXA SUPLEMENTAR DE SAÚDE - LEI N...      não provimento  
499  TRIBUTÁRIO - TAXA SUPLEMENTAR DE SAÚDE - LEI N...      não provimento  
500  TRIBUTÁRIO - TAXA SUPLEMENTAR DE SAÚDE - LEI N...      não provimento  

[501 rows x 10 columns]

In [21]:
df_int.to_excel('D:/HD_externo_yas/Faculdade/Assistencia_de_pesquisa/trf/Apelado/ANS.xlsx', index=False)